In [ ]:
import sys
sys.path.append("..")
from rnnlm_gen import RnnlmGen
from common.util import *

In [ ]:
import nltk
import numpy as np
import re
nltk.download('stopwords')
from nltk.corpus import stopwords
from pandas import read_csv
import collections
from sklearn.model_selection import train_test_split


dataset = read_csv('Womens Clothing E-Commerce Reviews.csv')
reviews = dataset['Review Text'].astype('str')
recommend = dataset['Recommended IND']


REPLACE_BY_SPACE_RE = re.compile('[/(){}\[\]\|@,;]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z #+_]')
STOPWORDS = set(stopwords.words('english'))


def review_prepare(review):
    review = review.lower()# lowercase text
    review = re.sub(REPLACE_BY_SPACE_RE," ",review)# replace REPLACE_BY_SPACE_RE symbols by space in text
    review = re.sub(BAD_SYMBOLS_RE,"",review)# delete symbols which are in BAD_SYMBOLS_RE from text
    review = re.sub(' +',' ',review)
    review = " ".join([word for word in review.split() if word not in STOPWORDS]) # delete stopwords from text
    return review

reviews_prepared = [review_prepare(review) for review in reviews]


In [ ]:
train = ".  ".join(reviews_prepared)
# 文章からコーパスを作る
copus, word_to_id, id_to_word = preprocess(train)

#ボキャブラリーサイズ　単語数
vocab_size = len(word_to_id)

corpus_size = len(copus)

In [ ]:
model = RnnlmGen()

In [ ]:
#start文字とskip文字の設定
start_word = "absolutely"
start_id = word_to_id[start_word]
#skip_words = ["N", "<unk>", "$"]
skip_words = []
skip_ids = [word_to_id[w] for w in skip_words]

# 未学習の初期値で出力

In [ ]:
#文章の生成
word_ids = model.generate(start_id, skip_ids)
txt = " ".join([id_to_word[i] for i in word_ids])
print(txt)

変な文章ですが、出力することができました

In [ ]:
# coding: utf-8
import sys
sys.path.append('..')
import numpy as np
import matplotlib.pyplot as plt
from dataset import sequence
from common.optimizer import Adam
from common.trainer import Trainer
from common.util import eval_seq2seq
from seq2seq import Seq2seq
from peeky_seq2seq import PeekySeq2seq


# データセットの読み込み
(x_train, t_train), (x_test, t_test) = sequence.load_data('addition.txt')
char_to_id, id_to_char = sequence.get_vocab()

# Reverse input? =================================================
is_reverse = False  # True
if is_reverse:
    x_train, x_test = x_train[:, ::-1], x_test[:, ::-1]
# ================================================================

# ハイパーパラメータの設定
vocab_size = len(char_to_id)
wordvec_size = 16
hideen_size = 128
batch_size = 128
max_epoch = 25
max_grad = 5.0

# Normal or Peeky? ==============================================
model = Seq2seq(vocab_size, wordvec_size, hideen_size)
# model = PeekySeq2seq(vocab_size, wordvec_size, hideen_size)
# ================================================================
optimizer = Adam()
trainer = Trainer(model, optimizer)

acc_list = []
for epoch in range(max_epoch):
    trainer.fit(x_train, t_train, max_epoch=1,
                batch_size=batch_size, max_grad=max_grad)

    correct_num = 0
    for i in range(len(x_test)):
        question, correct = x_test[[i]], t_test[[i]]
        verbose = i < 10
        correct_num += eval_seq2seq(model, question, correct,
                                    id_to_char, verbose, is_reverse)

    acc = float(correct_num) / len(x_test)
    acc_list.append(acc)
    print('val acc %.3f%%' % (acc * 100))

# グラフの描画
x = np.arange(len(acc_list))
plt.plot(x, acc_list, marker='o')
plt.xlabel('epochs')
plt.ylabel('accuracy')
plt.ylim(0, 1.0)
plt.show()


In [ ]:
!python train.py

In [ ]:
from dataset import sequence

In [ ]:
(x_train, t_train), (x_test, t_test) = sequence.load_data('addition.txt')

In [ ]:
! python train.py

['', '', '', '', '', '', '', '', '<!DOCTYPE html>', '<html lang="en">', '  <head>', '    <meta charset="utf-8">', '  <link rel="dns-prefetch" href="https://assets-cdn.github.com">', '  <link rel="dns-prefetch" href="https://avatars0.githubusercontent.com">', '  <link rel="dns-prefetch" href="https://avatars1.githubusercontent.com">', '  <link rel="dns-prefetch" href="https://avatars2.githubusercontent.com">', '  <link rel="dns-prefetch" href="https://avatars3.githubusercontent.com">', '  <link rel="dns-prefetch" href="https://github-cloud.s3.amazonaws.com">', '  <link rel="dns-prefetch" href="https://user-images.githubusercontent.com/">', '', '', '', '  <link crossorigin="anonymous" media="all" integrity="sha512-mjQPRAh2Y9A0sPdZzipNfPO7PT4g06mk0uZs15DbL/vsNCRGx1uRzWVzls9MJCoy2yRNjaMmEVFKJDpCui00mA==" rel="stylesheet" href="https://assets-cdn.github.com/assets/frameworks-df973073d880f28fbbae0263fb1ef62b.css" />', '  <link crossorigin="anonymous" media="all" integrity="sha512-x3XWtGp2Fsw